In [ ]:
import json
import math
import numpy as np
from rustworkx import PyGraph

from quantum_flows import quantum_flows
from qiskit import QuantumCircuit, QuantumRegister, ClassicalRegister
from qiskit.circuit import Parameter
from qiskit.qasm2 import dumps
from qiskit.quantum_info import Operator, Pauli, PauliList, SparsePauliOp
from qiskit.visualization import circuit_drawer

from qiskit_nature.second_q.hamiltonians.lattices import KagomeLattice, Lattice, LineLattice, HexagonalLattice, HyperCubicLattice, SquareLattice, TriangularLattice
from qiskit_nature.second_q.hamiltonians.lattices.boundary_condition import BoundaryCondition
from qiskit_optimization import QuadraticProgram

In [ ]:
# a simple quantum circuit
cr = ClassicalRegister(2)
qr = QuantumRegister(2)
qc = QuantumCircuit(qr, cr)
qc.h(qr[0])
qc.x(qr[1])
qc.measure(0, 0)
qc.measure(1, 1)
qc.draw()

In [ ]:
# a parametrized quantum circuit
cr = ClassicalRegister(2)
qr = QuantumRegister(2)
pqc = QuantumCircuit(qr, cr)
theta = Parameter('θ')
phi = Parameter('φ')
lam = Parameter('λ')
pqc.ry(theta, 0)
pqc.rx(phi, 1)
pqc.ry(lam, 0)
pqc.measure(0, 0)
pqc.measure(1, 1)
pqc.draw()

In [ ]:
# instantiate a provider
provider = quantum_flows.QuantumFlowsProvider()

In [ ]:
# authenticate with the Quantum Flows platform. In case o failure try a second time
provider.authenticate()

In [ ]:
# get the list of supported backends
provider.get_backends()

## Basic Usage: Creating Regular Jobs

In [ ]:
# performing sampling on a circuit
job = provider.submit_job(backend="aer-simulator", circuit=qc, shots=100, comments="Sending a job with a single circuit.")

In [ ]:
# performing sampling on a list of circuits
job = provider.submit_job(backend="aer-simulator", circuits=[qc, qc], shots=100, comments="Sending a job with list or circuits.")

In [ ]:
provider.get_job_status(job)

In [ ]:
provider.get_job_result(job)

## Advanced Usage: Creating Workflow Jobs

### Sending PUB objects for sampling

#### A primitive unified bloc (PUB) is a tuple formed a circuit, optionally circuit paramters as a list of reals, and optionally a number of shots

In [ ]:
# Case 1: input pub is a circuit:
input_data = quantum_flows.InputData(label="pub", content=qc)

# Case 2: input pub is a tuple containing  a circuit:
input_data.add_data(label="pub", content=(qc,))

# Case 3: input pub is a tuple containing a parametrized circuit and a list of paramater values:
input_data.add_data(label="pub", content=(pqc, [0.1, 0.2, 0.3]))

# Case 4: input pub is a tuple containing a parametrized circuit, a list of paramater values and a number of shots:
input_data.add_data(label="pub", content=(pqc, [1.1, 1.2, 1.3], 256))

In [ ]:
# comments are optional arguments
workflow_job = provider.submit_workflow_job(backend="aer-simulator", shots=100, workflow_id="add-wf-id-her", input_data=input_data, comments="Sampling job")

### Computing the expectation value or the variance of operators

In [ ]:
matrix = np.array([[1, 0, 0, 0],
                   [0, -1, 0, 0],
                   [0, 0, -1, 0],
                   [0, 0, 0, 1]]) 
operator = Operator(matrix)

In [ ]:
input_data = quantum_flows.InputData(label="operator", content=operator)
input_data.add_data(label="pub", content=(qc,))

In [ ]:
# comments are optional arguments
workflow_job = provider.submit_workflow_job(backend="aer-simulator", shots=100, workflow_id="add-wf-id-here", input_data=input_data, comments="Expectation value job")

### Computing the ground state for a molecule using VQE

In [ ]:
# checkout MoleculeInfo data class in Qiskit Nature
molecule_info = {
    "symbols": ['H', 'H'],
    "coords": [(0, 0, 0), (0, 0, 0.735)],
    "multiplicity": 1,   # optional
    "charge": 0,         # optional
    "units": "Angstrom", # optional
    "masses": [1.00784, 1.00784] # optional
}

In [ ]:
input_data = quantum_flows.InputData(label="molecule-info", content=molecule_info)

In [ ]:
# comments and max_iterations are optional arguments
workflow_job = provider.submit_workflow_job(backend="aer-simulator", shots=10000, workflow_id="add-wf-id-here", input_data=input_data, comments="VQE job", max_iterations=200)

### Computing the ground state for a molecule using VQE with input ansatz paramaters

In [ ]:
molecule_info = {
    "symbols": ['H', 'H'],
    "coords": [(0, 0, 0), (0, 0, 0.735)],
    "multiplicity": 1,   # optional
    "charge": 0,         # optional
    "units": "Angstrom", # optional
    "masses": [1.00784, 1.00784] # optional
}

In [ ]:
input_data = quantum_flows.InputData(label="molecule-info", content=molecule_info)

In [ ]:
input_data.add_data(label="ansatz-parameters", content=[9.830635517094142e-07, 2.4867962696595802e-05, -0.11164769628713214])

In [ ]:
# comments and max_iterations are optional arguments
workflow_job = provider.submit_workflow_job(backend="aer-simulator", shots=100, workflow_id="add-wf-id-here", input_data=input_data, comments="VQE job with input params", max_iterations=200)

### Solving optimization problems (Quadratic Program input)

In [ ]:
Q = np.array([
    [ 1.0, -2.0,  0.0],
    [-2.0,  4.0, -1.0],
    [ 0.0, -1.0,  2.0],
])
c = np.array([3.0, 0.0, 1.0])   # optional linear term
offset = 5.0                    # optional constant term
n = Q.shape[0]
qp = QuadraticProgram("my_qubo")
for i in range(n):
    qp.binary_var(f"x{i}")

qp.minimize(constant=offset, linear=c, quadratic=Q)

In [ ]:
input_data = quantum_flows.InputData(label="quadratic-program", content=qp)

In [ ]:
# comments and max_iterations are optional arguments
workflow_job = provider.submit_workflow_job(backend="fake_brisbane", shots=100, workflow_id="add-wf-id-here", input_data=input_data, comments="Quadratic Program input", max_iterations=200)

### Solving optimization problems (LP model input)

In [ ]:
# Note that a QuadraticProgram can be casted to lp format via export_as_lp_string() method
lp_model = """Minimize
 obj: x + 2 y
Subject To
 c1: x - y = 3

Bounds
 0 <= x <= 1
 -1 <= y <= 5

Binaries
 x
 y

End
"""

In [ ]:
input_data = quantum_flows.InputData(label="lp-model", content=lp_model)

In [ ]:
# comments and max_iterations are optional arguments
workflow_job = provider.submit_workflow_job(backend="aer-simulator", shots=100, workflow_id="add-wf-id-here", input_data=input_data, comments="LP model input", max_iterations=200)

### Solving optimization problems (Ising model input)

In [ ]:
# Note that the hamiltonian will be reconstructed with a minus sign in front of each term: H = -Sum(h_i * Z_i) - Sum(J_ij * Z_i Z_j)
ising_model = {
    "h": [3, -2, 1],
    "J": [
        {"pair": [0, 1], "value": -1},
        {"pair": [1, 2], "value": 2}
    ]
}

In [ ]:
input_data = quantum_flows.InputData(label="ising-model", content=ising_model)

In [ ]:
# comments and max_iterations are optional arguments
workflow_job = provider.submit_workflow_job(backend="aer-simulator", shots=100, workflow_id="add-wf-id-her", input_data=input_data, comments="Ising input", max_iterations=200)

### Computing the ground state for a lattice using VQE

In [ ]:
lattice = LineLattice(num_nodes=2, boundary_condition=BoundaryCondition.OPEN)
input_data = quantum_flows.InputData(label="lattice", content=lattice)

# other lattice models
lattice = SquareLattice(2, 3, boundary_condition=(BoundaryCondition.OPEN, BoundaryCondition.PERIODIC))
lattice = TriangularLattice(rows=2, cols=3, boundary_condition=BoundaryCondition.PERIODIC)
lattice = HexagonalLattice(rows=2, cols=3, edge_parameter=1.0 + 0.5j, onsite_parameter=2.0,)
lattice = KagomeLattice(2, 3, boundary_condition=BoundaryCondition.PERIODIC)
graph = PyGraph(multigraph=False)
graph.add_nodes_from(range(6))
weighted_edge_list = [
    (0, 1, 1.0 + 1.0j),
    (0, 2, -1.0),
    (2, 3, 2.0),
    (2, 4, -1.0),
    (4, 4, 3.0),
    (2, 5, -1.0),
]
graph.add_edges_from(weighted_edge_list)
lattice = Lattice(graph)

In [ ]:
# comments and max_iterations are optional arguments
workflow_job = provider.submit_workflow_job(backend="aer-simulator", shots=10000, workflow_id="add-wf-id-here", input_data=input_data, comments="VQE lattice", max_iterations=200)

### Quantum neural network classifier

In [ ]:
training_data = [
  { "data-point": [0.5479121, -0.12224312], "label": 1 },
  { "data-point": [0.71719584, 0.39473606], "label": 1 },
  { "data-point": [-0.8116453, 0.9512447], "label": 1 },
  { "data-point": [0.5222794, 0.57212861], "label": 1 },
  { "data-point": [-0.74377273, -0.09922812], "label": -1 },
  { "data-point": [-0.25840395, 0.85352998], "label": 1 },
  { "data-point": [0.28773024, 0.64552323], "label": 1 },
  { "data-point": [-0.1131716, -0.54552256], "label": -1 },
  { "data-point": [0.10916957, -0.87236549], "label": -1 },
  { "data-point": [0.65526234, 0.2633288], "label": 1 },
  { "data-point": [0.51617548, -0.29094806], "label": 1 },
  { "data-point": [0.94139605, 0.78624224], "label": 1 },
  { "data-point": [0.55676699, -0.61072258], "label": -1 },
  { "data-point": [-0.06655799, -0.91239247], "label": -1 },
  { "data-point": [-0.69142102, 0.36609791], "label": -1 },
  { "data-point": [0.48952431, 0.93501946], "label": 1 },
  { "data-point": [-0.34834928, -0.25908059], "label": -1 },
  { "data-point": [-0.06088838, -0.62105728], "label": -1 },
  { "data-point": [-0.74015699, -0.04859015], "label": -1 },
  { "data-point": [-0.5461813, 0.33962799], "label": -1 }
]

In [ ]:
inference_data = [
  { "data-point": [0.2479121, -0.22224312] },
  { "data-point": [0.4479121, +0.12224312] },
  { "data-point": [0.3479121, -0.22224312] },
  { "data-point": [0.2479121, -0.02224312] },
  { "data-point": [0.9479121, +0.32224312] },
  { "data-point": [0.3479121, -0.22224312] },
  { "data-point": [0.2479121, -0.72224312] },
  { "data-point": [-0.1479121, +0.32224312] },
  { "data-point": [-0.8479121, +0.12224312] },
  { "data-point": [-0.9479121, -0.09224312] },
]

In [ ]:
input_data = quantum_flows.InputData(label="training-data", content=training_data)
input_data.add_data(label="inference-data", content=inference_data)
# comments and max_iterations are optional arguments
workflow_job = provider.submit_workflow_job(backend="aer-simulator", shots=10000, workflow_id="add-wf-id-here", input_data=input_data, comments="ML workflow", max_iterations=200)

### Quantum neural network regressor

In [ ]:
input_data = quantum_flows.InputData(label="training-data", content=training_data)
input_data.add_data(label="inference-data", content=inference_data)
# comments and max_iterations are optional arguments
workflow_job = provider.submit_workflow_job(backend="aer-simulator", shots=10000, workflow_id="add-wf-id-here", input_data=input_data, comments="NN Regressor", max_iterations=200)

### Quantum neural network sampler

In [ ]:
input_data = quantum_flows.InputData(label="training-data", content=training_data)
input_data.add_data(label="inference-data", content=inference_data)
input_data.add_data(label="ansatz-parameters", content=["array", "with", "ansatz", "intialization",  "parameters"])
# comments are optional arguments
workflow_job = provider.submit_workflow_job(backend="aer-simulator", shots=10000, workflow_id="add-wf-id-here", input_data=input_data, comments="NN Sampler")

### Quantum neural network estimator

In [ ]:
input_data = quantum_flows.InputData(label="training-data", content=training_data)
input_data.add_data(label="inference-data", content=inference_data)
input_data.add_data(label="ansatz-parameters", content=["array", "with", "ansatz", "intialization",  "parameters"])
# comments are optional arguments
workflow_job = provider.submit_workflow_job(backend="aer-simulator", shots=10000, workflow_id="add-wf-id-here", input_data=input_data, comments="NN Estimator")